In [ ]:
! pip install pykeen
! pip install torch

In [3]:
from pykeen.models import ERModel, TransE, DistMult
from pykeen.nn import Embedding
from pykeen.nn.modules import Interaction, NormBasedInteraction
from torch import FloatTensor
from pykeen.pipeline import pipeline
from class_resolver import Hint, HintOrType, OptionalKwargs
from torch.nn import functional
from pykeen.nn.init import xavier_uniform_, xavier_uniform_norm_, xavier_normal_norm_
from pykeen.typing import Constrainer, Initializer
from pykeen.regularizers import Regularizer, LpRegularizer
from typing import Union, Any, ClassVar, Mapping
from pykeen.utils import negative_norm_of_sum, tensor_product
from pykeen.constants import DEFAULT_EMBEDDING_HPO_EMBEDDING_DIM_RANGE
from pykeen.evaluation import RankBasedEvaluator
from pykeen.datasets.nations import NATIONS_TRAIN_PATH, NATIONS_TEST_PATH, NATIONS_VALIDATE_PATH
from pykeen.predict import predict_triples
import networkx as nx
from pykeen.datasets import FB15k237

INFO:pykeen.utils:Using opt_einsum


In [30]:
def filter_by_pagerank(data_file, threshold):
    kg = nx.MultiDiGraph()
    filtered_triplets = []
    with open(data_file, 'r') as f:
        for line in f:
            head, relation, tail = line.strip().split('\t')
            kg.add_edge(head, tail, label = relation)

    centrality_scores = nx.pagerank(kg)

    for head, tail, relation in kg.edges(data=True):
        if centrality_scores[head] >= threshold and centrality_scores[tail] >= threshold:
            filtered_triplets.append((head, relation['label'], tail))

    with open('train.txt', 'w') as f:
        for head, relation, tail in filtered_triplets:
            f.write(f"{head}\t{relation}\t{tail}\n")

    return filtered_triplets


def kgcmodel_interaction(
    h: FloatTensor,
    r: FloatTensor,
    t: FloatTensor,
    p: Union[int, str] = 2,
    power_norm: bool = False,
) -> FloatTensor:
    return (tensor_product(h, r, t).sum(dim=-1) * negative_norm_of_sum(h, r, -t, p=p, power_norm=power_norm))

class KGCModelInteraction(NormBasedInteraction[FloatTensor, FloatTensor, FloatTensor]):

    func = kgcmodel_interaction


class KGCModel(ERModel):

    hpo_default: ClassVar[Mapping[str, Any]] = dict(
        embedding_dim=DEFAULT_EMBEDDING_HPO_EMBEDDING_DIM_RANGE,
        scoring_fct_norm=dict(type=int, low=1, high=2),
    )

    def __init__(
        self,
        *,
        embedding_dim: int = 50,
        scoring_fct_norm: int = 1,
        entity_initializer: Hint[Initializer] = xavier_uniform_,
        entity_constrainer: Hint[Constrainer] = functional.normalize,
        relation_initializer: Hint[Initializer] = xavier_uniform_norm_,
        relation_constrainer: Hint[Constrainer] = None,
        regularizer: HintOrType[Regularizer] = LpRegularizer,
        regularizer_kwargs: OptionalKwargs = None,
        **kwargs,
    ) -> None:

        if regularizer is LpRegularizer and regularizer_kwargs is None:
            regularizer_kwargs = DistMult.regularizer_default_kwargs

        super().__init__(
            interaction=KGCModelInteraction,
            interaction_kwargs=dict(p=scoring_fct_norm),
            entity_representations=Embedding,
            entity_representations_kwargs=dict(
                embedding_dim=embedding_dim,
                initializer=entity_initializer,
                constrainer=entity_constrainer,
            ),
            relation_representations=Embedding,
            relation_representations_kwargs=dict(
                embedding_dim=embedding_dim,
                initializer=relation_initializer,
                constrainer=relation_constrainer,
                regularizer=regularizer,
                regularizer_kwargs=regularizer_kwargs,
            ),
            **kwargs,
        )

## Результаты KGCModel без фильтрации

### Nations

In [31]:
result_KGCModel = pipeline(
    model=KGCModel,
    model_kwargs={'embedding_dim': 50},
    training=NATIONS_TRAIN_PATH,
    testing=NATIONS_TEST_PATH,
    validation=NATIONS_VALIDATE_PATH,
    optimizer='Adam',
    loss='marginranking',
    loss_kwargs=dict(margin=1),
    training_kwargs={'num_epochs': 100},
    training_loop='sLCWA',
    evaluator = RankBasedEvaluator,
    random_seed=1603073093
)

print(f"MRR: {result_KGCModel.metric_results.to_flat_dict()['both.realistic.inverse_harmonic_mean_rank']}")
for k in [1,3,5,10]:
    print(f"Hits@{k} : {result_KGCModel.metric_results.to_flat_dict()['both.realistic.hits_at_'+str(k)]}")

INFO:pykeen.pipeline.api:Using device: None


Training epochs on cuda:0:   0%|          | 0/100 [00:00<?, ?epoch/s]

Training batches on cuda:0:   0%|          | 0/7 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/7 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/7 [00:00<?, ?batch/s]

...

Training batches on cuda:0:   0%|          | 0/7 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/7 [00:00<?, ?batch/s]

Evaluating on cuda:0:   0%|          | 0.00/201 [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 0.11s seconds


MRR: 0.6104003190994263
Hits@1 : 0.43781094527363185
Hits@3 : 0.7189054726368159
Hits@5 : 0.8159203980099502
Hits@10 : 0.9701492537313433


### FB15k-237

In [34]:
result_KGCModel = pipeline(
    model=KGCModel,
    model_kwargs={'embedding_dim': 50},
    training='/FB15k-237/train.txt',
    testing='/FB15k-237/test.txt',
    validation='/FB15k-237/valid.txt',
    optimizer='Adam',
    loss='marginranking',
    loss_kwargs=dict(margin=1),
    training_kwargs={'num_epochs': 100},
    training_loop='sLCWA',
    evaluator = RankBasedEvaluator,
    random_seed=1603073093
)

print(f"MRR: {result_KGCModel.metric_results.to_flat_dict()['both.realistic.inverse_harmonic_mean_rank']}")
for k in [1,3,5,10]:
    print(f"Hits@{k} : {result_KGCModel.metric_results.to_flat_dict()['both.realistic.hits_at_'+str(k)]}")

INFO:pykeen.pipeline.api:Using device: None


Training epochs on cuda:0:   0%|          | 0/100 [00:00<?, ?epoch/s]

Training batches on cuda:0:   0%|          | 0/1063 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1063 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1063 [00:00<?, ?batch/s]

...

Training batches on cuda:0:   0%|          | 0/1063 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1063 [00:00<?, ?batch/s]

Evaluating on cuda:0:   0%|          | 0.00/20.4k [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 9.52s seconds


MRR: 0.19223463535308838
Hits@1 : 0.11830903219493101
Hits@3 : 0.20669830707505626
Hits@5 : 0.26071533418142673
Hits@10 : 0.34482336823563947


## Результаты KGCModel с добавлением фильтрации

In [32]:
filtered_triplets = filter_by_pagerank(NATIONS_TRAIN_PATH, 0.04)

result_KGCModel = pipeline(
    model=KGCModel,
    model_kwargs={'embedding_dim': 50},
    training='/content/train.txt',
    testing=NATIONS_TEST_PATH,
    validation=NATIONS_VALIDATE_PATH,
    optimizer='Adam',
    loss='marginranking',
    loss_kwargs=dict(margin=1),
    training_kwargs={'num_epochs': 100},
    training_loop='sLCWA',
    evaluator = RankBasedEvaluator,
    random_seed=1603073093
)

print(f"MRR: {result_KGCModel.metric_results.to_flat_dict()['both.realistic.inverse_harmonic_mean_rank']}")
for k in [1,3,5,10]:
    print(f"Hits@{k} : {result_KGCModel.metric_results.to_flat_dict()['both.realistic.hits_at_'+str(k)]}")

INFO:pykeen.pipeline.api:Using device: None


Training epochs on cuda:0:   0%|          | 0/100 [00:00<?, ?epoch/s]

Training batches on cuda:0:   0%|          | 0/6 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/6 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/6 [00:00<?, ?batch/s]

...

Training batches on cuda:0:   0%|          | 0/6 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/6 [00:00<?, ?batch/s]

Evaluating on cuda:0:   0%|          | 0.00/164 [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 0.12s seconds


MRR: 0.672995388507843
Hits@1 : 0.5213414634146342
Hits@3 : 0.75
Hits@5 : 0.899390243902439
Hits@10 : 0.9969512195121951


In [33]:
filtered_triplets = filter_by_pagerank('/FB15k-237/train.txt', 2.500000000000001e-05)
print(len(filtered_triplets))

result_KGCModel = pipeline(
    model=KGCModel,
    model_kwargs={'embedding_dim': 50},
    training='/content/train.txt',
    testing='/FB15k-237/test.txt',
    validation='/FB15k-237/valid.txt',
    optimizer='Adam',
    loss='marginranking',
    loss_kwargs=dict(margin=1),
    training_kwargs={'num_epochs': 100},
    training_loop='sLCWA',
    evaluator = RankBasedEvaluator,
    random_seed=1603073093
)

print(f"MRR: {result_KGCModel.metric_results.to_flat_dict()['both.realistic.inverse_harmonic_mean_rank']}")
for k in [1,3,5,10]:
    print(f"Hits@{k} : {result_KGCModel.metric_results.to_flat_dict()['both.realistic.hits_at_'+str(k)]}")

231511


INFO:pykeen.pipeline.api:Using device: None


Training epochs on cuda:0:   0%|          | 0/100 [00:00<?, ?epoch/s]

Training batches on cuda:0:   0%|          | 0/905 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/905 [00:00<?, ?batch/s]

...

Training batches on cuda:0:   0%|          | 0/905 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/905 [00:00<?, ?batch/s]

Evaluating on cuda:0:   0%|          | 0.00/16.0k [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 5.85s seconds


MRR: 0.20952969789505005
Hits@1 : 0.1303803019860911
Hits@3 : 0.22824384437065348
Hits@5 : 0.28481924691435373
Hits@10 : 0.3725330493076875
